In [94]:
import panel as pn
import pandas as pd
from datetime import datetime, timedelta
import plotly.express as px
import holoviews as hv
import numpy as np
import random
import scipy.stats as stats
# pn.extension()
pn.extension('tabulator')
pn.extension('plotly')
pn.extension(template='fast')
pn.extension('perspective')
# pn.extension('echarts')
# pn.extension('vega')
import hvplot.pandas  # noqa
from sqlalchemy import create_engine
from script import api
# from backgroundTask import stocks_stream
from functools import partial
import plotly.graph_objects as go
from panel.viewable import Viewer
import param
# pn.extension('plotly')
db_url = 'sqlite:///instance/local.db'
engine = create_engine(db_url)

In [117]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [96]:
## config template
pn.template.FastListTemplate.site = ''
pn.template.FastListTemplate.title = '投资组合风险监测工具📈'

# define function in this section

In [97]:
def create_ts_scatter_plot(data: pd.DataFrame, options: dict={}):
    """
    create a time series scatter plot of the data
    hoter indicate more recent
    colder indicate less recent
    data: only accept three columns·········: date, x, y
    """

    # Calculate the delta days from each data poin···t's date to the maximum date
    min_date = data['date'].min()
    data['delta_days'] = (data['date'] - min_date).dt.days
    
    # Define the colormap for the heatmap-like color scheme
    cmap = 'inferno'
    
    # Create the scatter plot with heatmap-like color scheme
    plot = data.hvplot.scatter(
        x='x',
        y='y',
        c='delta_days',
        cmap=cmap,
        **options
    )
    
    return plot


# layout in this section


In [98]:
# samllest date in eval_total
def create_date_range_slider(eval_total):
    start_date = eval_total['date'].min()
    end_date = eval_total['date'].max()
    date_range_slider = pn.widgets.DateRangeSlider(
        name='Date Range Slider',
        start= start_date, end=end_date,
        value=(start_date, end_date),
        step=1
    )
    return date_range_slider

In [99]:
def create_range_box(date_range, eval_total,aggregate_bnb_stock):
    '''display data within a range'''
    options = dict(width=500, shared_axes=False)
    active_tools = dict(tools=['hover'],active_tools=[])
    
    eval_total_range = eval_total[(eval_total['date']>=date_range[0]) & (eval_total['date']<=date_range[1])]
    aggregate_bnb_stock_range = aggregate_bnb_stock[(aggregate_bnb_stock['date']>=date_range[0]) & (aggregate_bnb_stock['date']<=date_range[1])]

    cum_pnl_trend = eval_total_range.hvplot.line(x='date', y=['cum_pnl'], title='cum_pnl_trend', **options)
    # risk 
    risk_trend = eval_total_range.hvplot.line(x='date',y=['risk'], title='risk_trend', **options)

    # tracking error
    tracking_error = eval_total_range.hvplot.line(x='date',y=['tracking_error'], title='tracking_error', **options)

    # bnb stock
    bnb_stock_plot = aggregate_bnb_stock_range.hvplot.bar(x='date',y=['allocation','selection','interaction','excess'], title='bnb_stock', **options,stacked=True)

    overview_box = pn.Column(cum_pnl_trend.opts(**active_tools), 
                             bnb_stock_plot.opts(**active_tools),
                             risk_trend.opts(**active_tools),
                             tracking_error.opts(**active_tools), ncols=1, height_policy="max", scroll=True)
    return overview_box

In [100]:
def create_single_date_box(date_type, bnb_sector, filterd_stock_bnb):
    options = dict(width=800, height=600,shared_axes=False, tools=["pan",'hover'])
    active_tools = dict(tools=['hover'],active_tools=[])
    date = datetime.combine(date_type, datetime.min.time())
    
    selected_bnb_sector =  bnb_sector[(bnb_sector['date']==date)]
    selected_filtered_stock_bnb = filterd_stock_bnb[(filterd_stock_bnb['date']==date)]
   
    
    # bnb sector 
    bnb_stock_plot = selected_filtered_stock_bnb.hvplot.bar(x='display_name',y=['interaction','selection','allocation'],rot=90, **options)
    bnb_sector_plot = selected_bnb_sector.hvplot.bar(x='aggregate_sector',y=['interaction','selection','allocation'], **options)
    overview_box = pn.Column(bnb_sector_plot.opts(**active_tools),
                             bnb_stock_plot.opts(**active_tools), height_policy='max',scroll=True)
    return overview_box



In [102]:
## main page 
# date range slider
def create_overview(eval_total, eval_sector, bnb_sector, bnb_stock, profile_p, profile_b, aggregate_bnb_stock): 
    date_range_slider = create_date_range_slider(eval_total)
    overview_box = pn.bind(create_range_box, date_range=date_range_slider, eval_total=eval_total,aggregate_bnb_stock=aggregate_bnb_stock)
    # date picker
    ts_list = list(eval_total['date'].unique())
    ava_days = [ts.date() for ts in  ts_list]
    date_picker = pn.widgets.DatePicker(name='Date Picker', value=datetime(2021,11,19).date(),enabled_dates=ava_days)

    single_date_box = pn.bind(create_single_date_box, date_type=date_picker, bnb_sector=bnb_sector, filterd_stock_bnb=bnb_stock)
    
    main_pn = pn.Row( 
        pn.Column(date_range_slider, overview_box, sizing_mode='stretch_height'),
        pn.Column(date_picker, single_date_box, sizing_mode="stretch_height")
        )
    return main_pn
# create_overview().servable(target='main')

In [103]:
# # load data
# calculated_p_stock = pd.read_pickle('./data/calculated_p_stock.pkl')
# calculated_b_stock = pd.read_pickle('./data/calculated_b_stock.pkl')
# p_eval_df = pd.read_pickle('./data/p_eval_df.pkl')
# sector_eval_df = pd.read_pickle('./data/sector_eval_df.pkl')
# merged_df = pd.read_pickle('./data/merged_df.pkl')
# bnb_sector_result = pd.read_pickle('./data/bnb_sector_result.pkl')
# bnb_stock_result = pd.read_pickle('./data/bnb_stock_result.pkl')
# profile_p = pd.read_pickle('./data/p_profile.pkl')
# profile_b = pd.read_pickle('./data/b_profile.pkl')




In [104]:
# merged_df.columns

In [105]:
# ## calculate sector allocation, interaction, selection
# def calculate_sector_attribution(calculated_p_stock, calculated_b_stock):
#     sector_view_p = calculated_p_stock.groupby(['date','aggregate_sector']).aggregate({'prev_w_in_p': 'sum', 'sector_pct': 'sum'})
#     sector_view_b = calculated_b_stock.groupby(['date','aggregate_sector']).aggregate({'prev_w_in_p': 'sum', 'sector_pct': 'sum'})

#     sector_view_p['weighted_return'] = sector_view_p.prev_w_in_p * sector_view_p.sector_pct
#     sector_view_b['weighted_return'] = sector_view_b.prev_w_in_p * sector_view_b.sector_pct

#     merged_df = pd.merge(sector_view_p, sector_view_b, left_index=True, right_index=True, how='outer', suffixes=['_b', '_p'])
#     merged_df.fillna(0, inplace=True)
#     merged_df['active_return'] = merged_df['weighted_return_p'] - merged_df['weighted_return_b']
#     merged_df['allocation'] = (merged_df.prev_w_in_p_p - merged_df.prev_w_in_p_b) * merged_df.sector_pct_b
#     merged_df['selection'] = (merged_df.sector_pct_p - merged_df.sector_pct_b) * merged_df.prev_w_in_p_b
#     merged_df['interaction'] = (merged_df.sector_pct_p - merged_df.sector_pct_b) * (merged_df.prev_w_in_p_p - merged_df.prev_w_in_p_b)
#     merged_df['notinal_return'] = merged_df.allocation + merged_df.selection + merged_df.interaction 
#     return merged_df.reset_index()



In [106]:

# def calculate_total_attribution(calculated_p_stock, calculated_b_stock):
#     merged_df = pd.merge(calculated_b_stock, calculated_p_stock, on=['date', 'ticker'], how='outer', suffixes=['_b', '_p'])
#     df = merged_df[['pct_p','pct_b','prev_w_in_p_p','prev_w_in_p_b','ticker','date']]
#     df.fillna(0, inplace=True)
#     df['active_return'] = df.pct_p * df.prev_w_in_p_p - df.pct_b * df.prev_w_in_p_b
#     # allocation
#     df['allocation'] = (df.prev_w_in_p_p - df.prev_w_in_p_b) * df.pct_b
#     df['selection'] = (df.pct_p - df.pct_b) * df.prev_w_in_p_b
#     df['interaction'] = (df.pct_p - df.pct_b) * (df.prev_w_in_p_p - df.prev_w_in_p_b)
#     df['notinal_return'] = df.allocation + df.selection + df.interaction

#     daily_bnb_result = df.groupby(['date']).aggregate({'allocation': 'sum', 'selection': 'sum', 'interaction': 'sum','notinal_return':'sum','active_return':'sum'})
#     daily_bnb_result['date'] = daily_bnb_result.index
    
#     return daily_bnb_result.reset_index(drop=True)


In [107]:
# def attribution_view(calculated_p_stock, calculated_b_stock, p_eval_df):
#     daily_bnb_result = calculate_total_attribution(calculated_p_stock, calculated_b_stock)
#     daily_sector_bnb_result = calculate_sector_attribution(calculated_p_stock, calculated_b_stock)
#     p_eval_df.date = pd.to_datetime(p_eval_df.date)
#     daily_bnb_result.date = pd.to_datetime(daily_bnb_result.date)
#     daily_sector_bnb_result.date = pd.to_datetime(daily_sector_bnb_result.date)
    
#     # interactive widget
#     dt_range = pn.widgets.DateRangeSlider(start=p_eval_df.date.min(), end=p_eval_df.date.max(), value=(p_eval_df.date.min(), p_eval_df.date.max()))
#     # total attribution and return
#     p_eval_df_i = p_eval_df.interactive()
#     daily_bnb_result_i = daily_bnb_result.interactive()
#     daily_return_plot = p_eval_df_i[(p_eval_df_i.date>=dt_range.param.value_start) & (p_eval_df_i.date<=dt_range.param.value_end)].hvplot(x='date',y=['portfolio_return_p','portfolio_return_b']).output()
#     daily_bnb_plot=daily_bnb_result_i[daily_bnb_result_i.date.between(dt_range.param.value_start, dt_range.param.value_end)]\
#         .hvplot.bar(x='date',y=['allocation', 'selection', 'interaction', "active_return"],stacked=True, title='每日主动收益组成', yformatter='%.2f', xlabel='日期',shared_axes=False).output()

#     # return
#     daily_sector_bnb_df_i = daily_sector_bnb_result.interactive()
#     selected_range_df = daily_sector_bnb_df_i[daily_sector_bnb_df_i.date.between(dt_range.param.value_start, dt_range.param.value_end)]
#     sector_active_return_plot = selected_range_df.hvplot.line(x='date',y='active_return',by='aggregate_sector', width=1000, height=400, title='BHB Sector Attribution').output()

#     # attribution
#     def plot_attribute_by_sector(sector):
#         selected_sector_df = selected_range_df[selected_range_df.aggregate_sector == sector]
#         return selected_sector_df.hvplot.bar(x='date',y=['active_return','allocation','selection','interaction'],stacked=True, shared_axes=False).output()
#     sector_attr_plot_tabs = pn.Tabs(*[(sector,plot_attribute_by_sector(sector)) for sector in daily_sector_bnb_result.aggregate_sector.unique()], dymacic=True)

#     #layout 
#     sector_view = pn.Column(sector_attr_plot_tabs, sector_active_return_plot)
#     total_view = pn.Column(daily_return_plot,daily_bnb_plot)
#     return pn.Column(
#         pn.Row(dt_range),
#         pn.Row(total_view, sector_view)
#         )

In [108]:
# attribution_view(calculated_p_stock, calculated_b_stock, p_eval_df).servable(target='main')

In [109]:
# def create_app(eval_total, eval_sector, bnb_sector, bnb_stock, profile_p, profile_b, aggregate_bnb_stock):
#     aggregate_bnb_stock = bnb_stock.groupby(['date']).aggregate({'allocation': 'sum', 'selection': 'sum', 'interaction': 'sum','excess':'sum'}) 
#     aggregate_bnb_stock['date'] = aggregate_bnb_stock.index
#     aggregate_bnb_stock.reset_index(drop=True, inplace=True)
#     filterd_stock_bnb = bnb_stock[bnb_stock.ticker.isin(profile_p['ticker'])]
#     tabs = pn.Tabs(dynamic=True)
#     overview = create_overview(eval_total, eval_sector, bnb_sector, bnb_stock, profile_p, profile_b, aggregate_bnb_stock)
#     exploer = create_hvplot_explore(eval_total, eval_sector, bnb_sector, bnb_stock, profile_p, profile_b)

#     tabs = pn.Tabs(("overview", overview),("exploer", exploer))
#     return tabs

# # create_app(p_eval_df,)

In [110]:
# from streamz import Stream
# from script import processing
# # load result 
# b_stock = pd.read_pickle('./data/b_stocks.pkl')
# p_stock = pd.read_pickle('./data/p_stocks.pkl')
# p_profile = pd.read_pickle('./data/p_profile.pkl')
# b_profile = pd.read_pickle('./data/b_profile.pkl')

# def process_stock_price(tuple):
#     p_stocks,p_profile, b_stocks, b_profile = tuple
#     calculated_p_stock = processing.get_processing_result_of_stocks_df(p_stocks, p_profile)
#     calculated_b_stock = processing.get_processing_result_of_stocks_df(b_stocks, b_profile)
#     return (calculated_p_stock, calculated_b_stock, p_profile)

# def get_portfolio_anlaysis(tuple):
#     calculated_p_stock, calculated_b_stock, p_profile = tuple
#     p_eval_df = processing.get_portfolio_evaluation(calculated_p_stock, calculated_b_stock, p_profile)
#     return p_eval_df

# def accumulate(previous, current):
#     pp_stocks, _, pb_stocks, _ = previous
#     cp_stocks, cp_profile, cb_stocks, cb_profile = current
#     p_stocks = pd.concat([pp_stocks, cp_stocks])
#     b_stocks = pd.concat([pb_stocks, cb_stocks])
#     return (p_stocks, cp_profile, b_stocks, cb_profile)

# from_api = Stream()
# from_accumulate = from_api.accumulate(accumulate)
# from_process_stock_price = from_accumulate.map(process_stock_price)
# from_get_portfolio_analysis = from_process_stock_price.map(get_portfolio_anlaysis)

# def start_pipeline():
#     g_b_stock = b_stock.groupby('date')
#     g_p_stock = p_stock.groupby('date')
#     for (_, df1),(_, df2) in zip(g_b_stock, g_p_stock):
#         yield from_api.emit((df1, p_profile, df2, b_profile))
    

# from_get_portfolio_analysis.sink(lambda x: print(x, '\n','---------'))
# # pn.state.add_periodic_callback(start_pipeline, 2000, 5)
# # ini_p_stock = pd.DataFrame(columns=p_stock.columns)
# # ini_b_stock = pd.DataFrame(columns=b_stock.columns)
# count = 0
# gb_stock = b_stock.groupby('date')
# gp_stock = p_stock.groupby('date')
# # for (_, df1),(_, df2) in zip(gb_stock, gp_stock):
# #     if count > 100:
# #         break
# #     from_api.emit((df1, p_profile, df2, b_profile))
# #     count += 1
# # from_api.emit((ini_p_stock, p_profile, ini_b_stock, b_profile))
# # from_api.emit((p_stock, p_profile, b_stock, b_profile))

In [111]:
# ## load date
# with engine.connect() as connection:
#     calculated_b_stock = pd.read_sql('calculated_b_stock', con=connection)
#     calculated_p_stock = pd.read_sql('calculated_p_stock', con=connection)
#     p_eval_df = pd.read_sql('p_eval_result', con=connection)
#     sector_eval_df = pd.read_sql('sector_eval_result', con=connection)

In [112]:
# calculated_b_stock.columns

In [113]:
import appComponents
from datetime import timedelta
class App(param.Parameterized):

    calculated_b_stock = param.Parameter()
    calculated_p_stock = param.Parameter()
    p_eval_df = param.Parameter()
    sector_eval_df = param.Parameter()
    attribution_result_df=param.Parameter()
    s_attribution_result_df=param.Parameter()
    count = 0
    @param.depends('p_eval_df','sector_eval_df','calculated_b_stock','calculated_p_stock')
    def overview(self):
        self.count += 1
        if self.p_eval_df is None or self.sector_eval_df is None:
            return pn.Column('Loading...')
        
        data = [self.calculated_b_stock, self.calculated_p_stock, self.p_eval_df, self.sector_eval_df]
        overview_panel = appComponents.create_portfolio_overview(data)
        return overview_panel
    @param.depends('p_eval_df','attribution_result_df','s_attribution_result_df')
    def attribution_view(self):
        if self.p_eval_df is None or self.attribution_result_df is None or self.s_attribution_result_df is None:
            return pn.Column('Loading...')
        else:
            return appComponents.attribution_view(self.attribution_result_df, self.s_attribution_result_df, self.p_eval_df)

    @param.depends('calculated_b_stock','calculated_p_stock','p_eval_df','sector_eval_df','attribution_result_df','s_attribution_result_df')
    def explore_view(self):
        if self.calculated_b_stock is None or self.calculated_p_stock is None or self.p_eval_df is None or self.sector_eval_df is None or self.attribution_result_df is None or self.s_attribution_result_df is None:
            return pn.Column('Loading...')
        else:
            return appComponents.create_hvplot_explore(self.calculated_b_stock, self.calculated_p_stock, self.p_eval_df, self.sector_eval_df, self.attribution_result_df, self.s_attribution_result_df)
    
    def panel(self):
        overview_page = pn.param.ParamMethod(self.overview, lazy=True)
        attribution_view = pn.param.ParamMethod(self.attribution_view, lazy=True)
        plot_explore = pn.param.ParamMethod(self.explore_view, lazy=True)
        tabs = pn.Tabs(('概述', overview_page),
                        ('每日主动汇报归因', attribution_view),
                        ('数据探索工具', plot_explore), dynamic=True
                    )
        return tabs
    
    def update(self, data):
        self.calculated_b_stock = data['calculated_b_stock']
        self.calculated_p_stock = data['calculated_p_stock']
        self.p_eval_df = data['p_eval_df']
        self.sector_eval_df = data['sector_eval_df']



app = App()







In [114]:

def update():
    with engine.connect() as connection:
        calculated_b_stock = pd.read_sql('calculated_b_stock', con=connection)
        calculated_p_stock = pd.read_sql('calculated_p_stock', con=connection)
        p_eval_df = pd.read_sql('p_eval_result', con=connection)
        sector_eval_df = pd.read_sql('sector_eval_result', con=connection)
        attribution_result_df = pd.read_sql('attribution_result', con=connection)
        s_attribution_result_df =  pd.read_sql('s_attribution_result', con=connection)
        app.param.set_param(calculated_b_stock=calculated_b_stock,
                            calculated_p_stock=calculated_p_stock,
                            p_eval_df=p_eval_df,
                            sector_eval_df=sector_eval_df,
                            attribution_result_df=attribution_result_df,
                            s_attribution_result_df=s_attribution_result_df
                            )
update()
# pn.state.add_periodic_callback(update, 1, 1)
# pn.param.ParamMethod(app.param, ['calculated_b_stock', 'calculated_p_stock', 'p_eval_df','sector_eval_df'], callback=update)
app.panel().servable(target='main')

        

/Users/lamonkey/Desktop/risk monitor/script/processing.py:309: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['display_name_p'] = df['display_name_p'].fillna(df['display_name_b'])
/Users/lamonkey/Desktop/risk monitor/script/processing.py:310: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['display_name_b'] = df['display_name_b'].fillna(df['display_name_p'])
/Users/lamonkey/Desktop/risk monitor/script/processing.py:313: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

BokehModel(combine_events=True, render_bundle={'docs_json': {'5f6d2503-91ed-43a2-af8c-48be7b85459d': {'version…